In [1]:
import pandas as pd
import numpy as np
import random

def bin_rate(df, n_bins):
    highest = df.loc[df['High'].idxmax()]['High']
    lowest = df.loc[df['Low'].idxmin()]['Low']
    diff = highest - lowest
    bin_size = round(diff / n_bins, 2)
    return bin_size, highest, lowest

def bin_vol(df, n_bins):
    highest = df.loc[df['Vol'].idxmax()]['Vol']
    lowest = df.loc[df['Vol'].idxmin()]['Vol']
    diff = highest - lowest
    bin_size = round(diff / n_bins, 2)
    return bin_size, highest, lowest

def reward(amount, xt_1, xt_2):
    tc = 0.1 + abs(amount / 100) 
    r = (xt_2 / xt_1) * (amount - tc) - amount
    return r
    




In [2]:
df = pd.read_csv('EURUSD15.csv', sep=",")
df.head()

Date  Time     Open     High      Low    Close   Vol
0  2016.03.21  1:45  1.12747  1.12782  1.12741  1.12741   878
1  2016.03.21  2:00  1.12742  1.12843  1.12724  1.12803  1279
2  2016.03.21  2:15  1.12804  1.12829  1.12763  1.12785   875
3  2016.03.21  2:30  1.12786  1.12801  1.12720  1.12741   919
4  2016.03.21  2:45  1.12741  1.12790  1.12728  1.12769  1246

In [3]:
print(bin_rate(df, 10))
print(bin_vol(df, 100))

(0.02, 1.2555399999999999, 1.03249)
(141.98, 14199, 1)


In [4]:
class Counter(dict):
    """
    A counter keeps track of counts for a set of keys.

    The counter class is an extension of the standard python
    dictionary type.  It is specialized to have number values
    (integers or floats), and includes a handful of additional
    functions to ease the task of counting data.  In particular,
    all keys are defaulted to have value 0.  Using a dictionary:

    a = {}
    print a['test']

    would give an error, while the Counter class analogue:

    >>> a = Counter()
    >>> print a['test']
    0

    returns the default 0 value. Note that to reference a key
    that you know is contained in the counter,
    you can still use the dictionary syntax:

    >>> a = Counter()
    >>> a['test'] = 2
    >>> print a['test']
    2

    This is very useful for counting things without initializing their counts,
    see for example:

    >>> a['blah'] += 1
    >>> print a['blah']
    1

    The counter also includes additional functionality useful in implementing
    the classifiers for this assignment.  Two counters can be added,
    subtracted or multiplied together.  See below for details.  They can
    also be normalized and their total count and arg max can be extracted.
    """

    def __getitem__(self, idx):
        self.setdefault(idx, 0)
        return dict.__getitem__(self, idx)

    def incrementAll(self, keys, count):
        """
        Increments all elements of keys by the same count.

        >>> a = Counter()
        >>> a.incrementAll(['one','two', 'three'], 1)
        >>> a['one']
        1
        >>> a['two']
        1
        """
        for key in keys:
            self[key] += count

    def argMax(self):
        """
        Returns the key with the highest value.
        """
        if len(list(self.keys())) == 0:
            return None
        all = list(self.items())
        values = [x[1] for x in all]
        maxIndex = values.index(max(values))
        return all[maxIndex][0]

    def sortedKeys(self):
        """
        Returns a list of keys sorted by their values.  Keys
        with the highest values will appear first.

        >>> a = Counter()
        >>> a['first'] = -2
        >>> a['second'] = 4
        >>> a['third'] = 1
        >>> a.sortedKeys()
        ['second', 'third', 'first']
        """
        sortedItems = list(self.items())

        def compare(x, y): return sign(y[1] - x[1])
        sortedItems.sort(cmp=compare)
        return [x[0] for x in sortedItems]

    def totalCount(self):
        """
        Returns the sum of counts for all keys.
        """
        return sum(self.values())

    def normalize(self):
        """
        Edits the counter such that the total count of all
        keys sums to 1.  The ratio of counts for all keys
        will remain the same. Note that normalizing an empty
        Counter will result in an error.
        """
        total = float(self.totalCount())
        if total == 0:
            return
        for key in list(self.keys()):
            self[key] = self[key] / total

    def divideAll(self, divisor):
        """
        Divides all counts by divisor
        """
        divisor = float(divisor)
        for key in self:
            self[key] /= divisor

    def copy(self):
        """
        Returns a copy of the counter
        """
        return Counter(dict.copy(self))

    def __mul__(self, y):
        """
        Multiplying two counters gives the dot product of their vectors where
        each unique label is a vector element.

        >>> a = Counter()
        >>> b = Counter()
        >>> a['first'] = -2
        >>> a['second'] = 4
        >>> b['first'] = 3
        >>> b['second'] = 5
        >>> a['third'] = 1.5
        >>> a['fourth'] = 2.5
        >>> a * b
        14
        """
        sum = 0
        x = self
        if len(x) > len(y):
            x, y = y, x
        for key in x:
            if key not in y:
                continue
            sum += x[key] * y[key]
        return sum

    def __radd__(self, y):
        """
        Adding another counter to a counter increments the current counter
        by the values stored in the second counter.

        >>> a = Counter()
        >>> b = Counter()
        >>> a['first'] = -2
        >>> a['second'] = 4
        >>> b['first'] = 3
        >>> b['third'] = 1
        >>> a += b
        >>> a['first']
        1
        """
        for key, value in list(y.items()):
            self[key] += value

    def __add__(self, y):
        """
        Adding two counters gives a counter with the union of all keys and
        counts of the second added to counts of the first.

        >>> a = Counter()
        >>> b = Counter()
        >>> a['first'] = -2
        >>> a['second'] = 4
        >>> b['first'] = 3
        >>> b['third'] = 1
        >>> (a + b)['first']
        1
        """
        addend = Counter()
        for key in self:
            if key in y:
                addend[key] = self[key] + y[key]
            else:
                addend[key] = self[key]
        for key in y:
            if key in self:
                continue
            addend[key] = y[key]
        return addend

    def __sub__(self, y):
        """
        Subtracting a counter from another gives a counter with the union of all keys and
        counts of the second subtracted from counts of the first.

        >>> a = Counter()
        >>> b = Counter()
        >>> a['first'] = -2
        >>> a['second'] = 4
        >>> b['first'] = 3
        >>> b['third'] = 1
        >>> (a - b)['first']
        -5
        """
        addend = Counter()
        for key in self:
            if key in y:
                addend[key] = self[key] - y[key]
            else:
                addend[key] = self[key]
        for key in y:
            if key in self:
                continue
            addend[key] = -1 * y[key]
        return addend

In [48]:
import random

def flipCoin(p):
    r = random.random()
    return r < p

bins = [df.loc[df.head(8000)['Low'].idxmin()]['Low']]

for i in range(20):
    bins.append(bins[-1] + bin_rate(df, 20)[0])

    
    
def main(capital, iterations, alpha, amount,disc):
    qVals= Counter()
    vVals = Counter()
  
    for i in range(iterations):
        
        for t in range(len(df['Open'].head(8000)) - 1):
            
            for b in bins:
                if df['Open'][t] < b:
                    respective_bin = b
                    break
                    
            x_t =  df['Open'][t]  
            x_t1 =  df['Open'][t + 1] 
            for b in bins:
                if df['Open'][t + 1] < b:
                    respective_bin_2 = b
                    break
            
            for invest in range(1, amount, 1000):
                
                state = (respective_bin, invest)
                next_state = (respective_bin_2, random.choice(range(1, amount, 1000)))
                
                if flipCoin(0.1):
                    yes = (1 - alpha) * qVals[(state,'yes')] + alpha * (reward(invest, x_t, x_t1) + disc * random.choice([qVals[(next_state,'yes')], qVals[(next_state,'no')]]))
                    no = (1 - alpha) * qVals[(state,'no')] + disc * random.choice([qVals[(next_state,'yes')], qVals[(next_state,'no')]])
                else:
                    yes = (1 - alpha) * qVals[(state,'yes')] + alpha * (reward(invest, x_t, x_t1) + disc * vVals[(next_state)])
                    no = (1 - alpha) * qVals[(state,'no')] + disc * vVals[(next_state)]

                qVals[(state,'yes')] = yes
                qVals[(state,'no')] = no    

                if yes > no:
                    vVals[(state)] = yes
                else:
                    vVals[(state)] = no
        print(i)
        print(qVals)
        
    return qVals, vVals
                
            

In [49]:
the_qvals = main(0, 100, 0.5, 100000, 0.5)

0
{((1.13113, 1), 'yes'): -159.13195065140064, ((1.13113, 1), 'no'): -318.03483634615236, ((1.13113, 1001), 'yes'): -184.05450699401953, ((1.13113, 80001), 'yes'): -1254.1630839421773, ((1.13113, 80001), 'no'): -492.1347994460174, ((1.13113, 1001), 'no'): -342.684744927357, ((1.13113, 2001), 'yes'): -196.2071512412689, ((1.13113, 2001), 'no'): -386.6440452679239, ((1.13113, 3001), 'yes'): -192.78638294205686, ((1.13113, 3001), 'no'): -309.7510240901279, ((1.13113, 4001), 'yes'): -198.53543954533268, ((1.13113, 4001), 'no'): -296.04799597120507, ((1.13113, 5001), 'yes'): -224.24429798694925, ((1.13113, 5001), 'no'): -468.71487339071564, ((1.13113, 6001), 'yes'): -229.67042274360787, ((1.13113, 6001), 'no'): -307.91885798047684, ((1.13113, 7001), 'yes'): -241.78037410304347, ((1.13113, 7001), 'no'): -306.93920850587506, ((1.13113, 8001), 'yes'): -276.6456668072032, ((1.13113, 8001), 'no'): -351.4960006195952, ((1.13113, 9001), 'yes'): -288.14173287339435, ((1.13113, 9001), 'no'): -349.25

1
{((1.13113, 1), 'yes'): -188.47166422225172, ((1.13113, 1), 'no'): -375.9265271533153, ((1.13113, 1001), 'yes'): -179.4524848988238, ((1.13113, 80001), 'yes'): -1171.873122685706, ((1.13113, 80001), 'no'): -327.5504375371969, ((1.13113, 1001), 'no'): -333.50525614858213, ((1.13113, 2001), 'yes'): -195.1495065298761, ((1.13113, 2001), 'no'): -339.6566629932624, ((1.13113, 3001), 'yes'): -215.14247615011038, ((1.13113, 3001), 'no'): -354.50891504168004, ((1.13113, 4001), 'yes'): -258.9581953425816, ((1.13113, 4001), 'no'): -416.8863606654329, ((1.13113, 5001), 'yes'): -230.9877950106174, ((1.13113, 5001), 'no'): -335.75315625937674, ((1.13113, 6001), 'yes'): -243.81995873694774, ((1.13113, 6001), 'no'): -336.22059863953245, ((1.13113, 7001), 'yes'): -245.46275782766293, ((1.13113, 7001), 'no'): -314.61647405646204, ((1.13113, 8001), 'yes'): -293.88291277530686, ((1.13113, 8001), 'no'): -385.94470268011656, ((1.13113, 9001), 'yes'): -319.18935511655764, ((1.13113, 9001), 'no'): -411.358

2
{((1.13113, 1), 'yes'): -217.76065106252372, ((1.13113, 1), 'no'): -435.29662820838564, ((1.13113, 1001), 'yes'): -179.9632140001471, ((1.13113, 80001), 'yes'): -1150.8793235462404, ((1.13113, 80001), 'no'): -287.68949925712434, ((1.13113, 1001), 'no'): -334.50226671501173, ((1.13113, 2001), 'yes'): -158.94606048571487, ((1.13113, 2001), 'no'): -267.3415258616377, ((1.13113, 3001), 'yes'): -192.83933627685778, ((1.13113, 3001), 'no'): -309.8553416672694, ((1.13113, 4001), 'yes'): -213.94479697213282, ((1.13113, 4001), 'no'): -326.86671082480336, ((1.13113, 5001), 'yes'): -234.35994962463224, ((1.13113, 5001), 'no'): -328.75857373680424, ((1.13113, 6001), 'yes'): -221.68061050889514, ((1.13113, 6001), 'no'): -291.73615417258793, ((1.13113, 7001), 'yes'): -258.08705600412884, ((1.13113, 7001), 'no'): -340.4990350124192, ((1.13113, 8001), 'yes'): -294.64355149531684, ((1.13113, 8001), 'no'): -327.392119626742, ((1.13113, 9001), 'yes'): -273.3190872796971, ((1.13113, 9001), 'no'): -376.8

3
{((1.13113, 1), 'yes'): -139.81532235028538, ((1.13113, 1), 'no'): -279.66388613783243, ((1.13113, 1001), 'yes'): -190.81036417349117, ((1.13113, 80001), 'yes'): -1225.2853943862294, ((1.13113, 80001), 'no'): -374.7206001387374, ((1.13113, 1001), 'no'): -356.1965018084412, ((1.13113, 2001), 'yes'): -187.23602394018457, ((1.13113, 2001), 'no'): -310.3706794319129, ((1.13113, 3001), 'yes'): -263.0779372832382, ((1.13113, 3001), 'no'): -424.5820070393827, ((1.13113, 4001), 'yes'): -225.57288619663106, ((1.13113, 4001), 'no'): -348.16316866678727, ((1.13113, 5001), 'yes'): -235.3347882037064, ((1.13113, 5001), 'no'): -344.44733052271647, ((1.13113, 6001), 'yes'): -239.15377174108573, ((1.13113, 6001), 'no'): -326.89254585003044, ((1.13113, 7001), 'yes'): -283.7400640524689, ((1.13113, 7001), 'no'): -395.20705852587184, ((1.13113, 8001), 'yes'): -284.5998949033717, ((1.13113, 8001), 'no'): -367.3800750797292, ((1.13113, 9001), 'yes'): -280.78761709956143, ((1.13113, 9001), 'no'): -334.554

4
{((1.13113, 1), 'yes'): -237.3579155599618, ((1.13113, 1), 'no'): -474.76465789980455, ((1.13113, 1001), 'yes'): -200.0987442028375, ((1.13113, 80001), 'yes'): -1180.2572224628857, ((1.13113, 80001), 'no'): -346.4817691798296, ((1.13113, 1001), 'no'): -413.63132004193255, ((1.13113, 2001), 'yes'): -201.81043339372104, ((1.13113, 2001), 'no'): -352.9970880811279, ((1.13113, 3001), 'yes'): -224.3006386456414, ((1.13113, 3001), 'no'): -372.77794697591287, ((1.13113, 4001), 'yes'): -217.30775302834542, ((1.13113, 4001), 'no'): -354.85303446686396, ((1.13113, 5001), 'yes'): -213.04441887713477, ((1.13113, 5001), 'no'): -299.17007871976386, ((1.13113, 6001), 'yes'): -235.32398248475346, ((1.13113, 6001), 'no'): -319.22638912156185, ((1.13113, 7001), 'yes'): -446.97030859925076, ((1.13113, 7001), 'no'): -563.9351330948439, ((1.13113, 8001), 'yes'): -291.505425906686, ((1.13113, 8001), 'no'): -431.7466868878565, ((1.13113, 9001), 'yes'): -292.055668138829, ((1.13113, 9001), 'no'): -357.12347

...

95
{((1.13113, 1), 'yes'): -197.46927297942025, ((1.13113, 1), 'no'): -277.0083101438596, ((1.13113, 1001), 'yes'): -121.52178701969912, ((1.13113, 80001), 'yes'): -1191.423429590966, ((1.13113, 80001), 'no'): -366.6637074232757, ((1.13113, 1001), 'no'): -217.64272580179144, ((1.13113, 2001), 'yes'): -208.853074463549, ((1.13113, 2001), 'no'): -385.84450755843574, ((1.13113, 3001), 'yes'): -224.92625272373195, ((1.13113, 3001), 'no'): -374.02877315724754, ((1.13113, 4001), 'yes'): -195.67126748083385, ((1.13113, 4001), 'no'): -290.320930328911, ((1.13113, 5001), 'yes'): -361.49158683795605, ((1.13113, 5001), 'no'): -596.7607390216716, ((1.13113, 6001), 'yes'): -243.8895051539335, ((1.13113, 6001), 'no'): -335.93981645340074, ((1.13113, 7001), 'yes'): -267.5530159675744, ((1.13113, 7001), 'no'): -351.3154545585574, ((1.13113, 8001), 'yes'): -292.7783513771285, ((1.13113, 8001), 'no'): -420.02778843270323, ((1.13113, 9001), 'yes'): -244.6478569230582, ((1.13113, 9001), 'no'): -262.272456

96
{((1.13113, 1), 'yes'): -153.112779040063, ((1.13113, 1), 'no'): -306.0009686652719, ((1.13113, 1001), 'yes'): -232.70988524726624, ((1.13113, 80001), 'yes'): -1165.1948075313978, ((1.13113, 80001), 'no'): -324.40364887935783, ((1.13113, 1001), 'no'): -439.3541934898341, ((1.13113, 2001), 'yes'): -209.75687590976526, ((1.13113, 2001), 'no'): -370.8327003798758, ((1.13113, 3001), 'yes'): -183.603326992213, ((1.13113, 3001), 'no'): -290.0634372819659, ((1.13113, 4001), 'yes'): -217.72109977206912, ((1.13113, 4001), 'no'): -334.4193164247861, ((1.13113, 5001), 'yes'): -232.02629890795316, ((1.13113, 5001), 'no'): -314.65746184834467, ((1.13113, 6001), 'yes'): -210.51179317700786, ((1.13113, 6001), 'no'): -269.60159884729933, ((1.13113, 7001), 'yes'): -259.8266837552449, ((1.13113, 7001), 'no'): -275.83075485332563, ((1.13113, 8001), 'yes'): -253.92555716941152, ((1.13113, 8001), 'no'): -306.0593678331525, ((1.13113, 9001), 'yes'): -262.1446612883429, ((1.13113, 9001), 'no'): -297.13812

97
{((1.13113, 1), 'yes'): -187.82235553341616, ((1.13113, 1), 'no'): -383.2641641184415, ((1.13113, 1001), 'yes'): -159.76022186285195, ((1.13113, 80001), 'yes'): -1162.1549977345521, ((1.13113, 80001), 'no'): -308.121145633025, ((1.13113, 1001), 'no'): -294.096479688708, ((1.13113, 2001), 'yes'): -184.40786895010822, ((1.13113, 2001), 'no'): -378.66601782107637, ((1.13113, 3001), 'yes'): -260.80957457422994, ((1.13113, 3001), 'no'): -470.23036215299527, ((1.13113, 4001), 'yes'): -186.94147827236324, ((1.13113, 4001), 'no'): -273.10665777782776, ((1.13113, 5001), 'yes'): -240.9105901552068, ((1.13113, 5001), 'no'): -355.59874499731416, ((1.13113, 6001), 'yes'): -231.24919333538048, ((1.13113, 6001), 'no'): -311.0338303050828, ((1.13113, 7001), 'yes'): -249.55061293097663, ((1.13113, 7001), 'no'): -284.1149573901469, ((1.13113, 8001), 'yes'): -261.75114483011964, ((1.13113, 8001), 'no'): -312.6195460117127, ((1.13113, 9001), 'yes'): -283.03480208167247, ((1.13113, 9001), 'no'): -340.73

98
{((1.13113, 1), 'yes'): -161.6861652612298, ((1.13113, 1), 'no'): -323.1482463323594, ((1.13113, 1001), 'yes'): -195.74571339388072, ((1.13113, 80001), 'yes'): -1153.9549079915319, ((1.13113, 80001), 'no'): -287.2065279533938, ((1.13113, 1001), 'no'): -366.0672031753835, ((1.13113, 2001), 'yes'): -191.31457418707674, ((1.13113, 2001), 'no'): -332.005369641973, ((1.13113, 3001), 'yes'): -216.07708499924752, ((1.13113, 3001), 'no'): -357.1449503832581, ((1.13113, 4001), 'yes'): -234.15779859378304, ((1.13113, 4001), 'no'): -367.2927107350495, ((1.13113, 5001), 'yes'): -214.6418916947243, ((1.13113, 5001), 'no'): -303.0514184062497, ((1.13113, 6001), 'yes'): -236.7851002229456, ((1.13113, 6001), 'no'): -322.1480461357101, ((1.13113, 7001), 'yes'): -272.05557004133834, ((1.13113, 7001), 'no'): -367.4936003593156, ((1.13113, 8001), 'yes'): -317.1659677099242, ((1.13113, 8001), 'no'): -432.509939441803, ((1.13113, 9001), 'yes'): -381.0394148209673, ((1.13113, 9001), 'no'): -364.3767752260

99
{((1.13113, 1), 'yes'): -154.5246082428232, ((1.13113, 1), 'no'): -394.85699653817534, ((1.13113, 1001), 'yes'): -198.33944613343243, ((1.13113, 80001), 'yes'): -1150.5072910507406, ((1.13113, 80001), 'no'): -284.82556452037517, ((1.13113, 1001), 'no'): -367.9622586698557, ((1.13113, 2001), 'yes'): -164.76535389963192, ((1.13113, 2001), 'no'): -278.9069290656378, ((1.13113, 3001), 'yes'): -197.87310120533658, ((1.13113, 3001), 'no'): -319.9259309670765, ((1.13113, 4001), 'yes'): -215.4233987960518, ((1.13113, 4001), 'no'): -510.8289146970159, ((1.13113, 5001), 'yes'): -251.3470765363133, ((1.13113, 5001), 'no'): -376.4717170900881, ((1.13113, 6001), 'yes'): -223.01361412240325, ((1.13113, 6001), 'no'): -294.6052414073855, ((1.13113, 7001), 'yes'): -251.50908288645212, ((1.13113, 7001), 'no'): -326.3966260726179, ((1.13113, 8001), 'yes'): -352.5395808061129, ((1.13113, 8001), 'no'): -443.24702035720486, ((1.13113, 9001), 'yes'): -287.9440231926029, ((1.13113, 9001), 'no'): -364.79152

In [50]:
bins

[1.09113,
 1.10113,
 1.11113,
 1.12113,
 1.13113,
 1.14113,
 1.15113,
 1.16113,
 1.17113,
 1.18113,
 1.19113,
 1.20113,
 1.21113,
 1.22113,
 1.23113,
 1.24113,
 1.25113,
 1.26113,
 1.27113,
 1.28113,
 1.29113]

In [ ]:
df2 = df.head(1000)
for i in range(len(df2['Open'])):
    for b in bins:
        if df2['Open'][i] < b:
            df2['Open'][i] = b
            break
df2.head()


In [11]:
df2.tail()

Date   Time     Open     High      Low    Close   Vol
995  2016.04.04  16:00  1.17249  1.14013  1.13928  1.13965  1920
996  2016.04.04  16:15  1.17249  1.14058  1.13958  1.14045  1885
997  2016.04.04  16:30  1.17249  1.14092  1.13982  1.14033  3115
998  2016.04.04  16:45  1.17249  1.14053  1.13967  1.13991  2654
999  2016.04.04  17:00  1.17249  1.14075  1.13833  1.13859  3181

In [12]:
# df3 = df.tail(1000)
# for i in df3:
#     for b in bins:
#         if i < b:
#             current = b
#             break
    

In [51]:
import configparser
account_id = 'id_goes_here'
access_token = 'key_goes_here
# v20 OANDA API - 3rd party
import json
from oandapyV20 import API    # the client
import oandapyV20.endpoints.trades as trades

config = configparser.ConfigParser()
config.read('oanda.cfg')

client = API(access_token=access_token)

In [56]:
import pandas as pd
import datetime
from dateutil import parser
import oandapyV20.endpoints.instruments as instruments

# The v20 api handles from times a little differently - be careful of the timezone

from oandapyV20.endpoints.pricing import PricingStream
import oandapyV20.endpoints.orders as orders
from oandapyV20.contrib.requests import MarketOrderRequest
from oandapyV20.exceptions import V20Error, StreamTerminated
        
class autoTrader(PricingStream): 
    def __init__(self,*args, **kwargs): 
        PricingStream.__init__(self, *args, **kwargs)
        self.ticks = 0 
        self.position = 0
        self.df = pd.DataFrame()
        self.units = 100000
        self.connected = False
        self.client = API(access_token=config['oanda']['access_token'])
    def create_order(self, units):
        order = orders.OrderCreate(accountID=config['oanda']['account_id'], data=MarketOrderRequest(instrument="EUR_USD", units=units).data)
        response = self.client.request(order)
        print('\t', response)
    def on_success(self, data):
        self.ticks += 1
        print("ticks = ", self.ticks)
        
        self.df = self.df.append(pd.DataFrame([{'time': data['time'],'closeoutAsk':data['closeoutAsk']}],
                                 index=[data["time"]]))
        
        self.df.index = pd.DatetimeIndex(self.df["time"])
        
        self.df['closeoutAsk'] = pd.to_numeric(self.df["closeoutAsk"],errors='ignore')
        
        dfr = self.df.resample('5s').last().bfill()
        
        print('closeout', dfr['closeoutAsk'][0], 'w')
        for b in bins:
            if dfr['closeoutAsk'][0] < b:
                close_ask = b
                break
        print('closeask', close_ask)
        print(dfr,' dfrdfr')
        best_y = -99999
        best_n = -99999
        amounty = 0
        
        for i in range(1, 100001, 1000):
            if the_qvals[0][(close_ask, i), 'yes'] > best_y:
                best_y = the_qvals[0][(close_ask, i), 'yes']
                amounty = i
           
            if the_qvals[0][(close_ask, i), 'no'] > best_n:
                best_n = the_qvals[0][(close_ask, i), 'no']
                
        
        if best_y > best_n:
            cur_pos = 1
            self.units = amounty
                
        else:
            cur_pos = 0
        print('y: ', best_y, ', n: ', best_n, ', amount: ', self.units, ', pos:', cur_pos)
        if cur_pos == 1:
            print("go long")
            if self.position == 0:
                self.create_order(self.units)
            elif self.position == -1:
                self.create_order(self.units * 2)
            self.position = 1
        
        if self.ticks == 750:
            print("close out the position")
            if self.position == 1:
                self.create_order(-self.units)
            elif self.position == -1:
                self.create_order(self.units)
            self.disconnect()
    def disconnect(self):
        self.connected=False
    def rates(self, account_id, instruments, **params):
        self.connected = True
        params = params or {}
        ignore_heartbeat = None
        if "ignore_heartbeat" in params:
            ignore_heartbeat = params["ignore_heartbeat"]
        while self.connected:
            response = self.client.request(self)
            for tick in response:
                if not self.connected:
                    break
                if not (ignore_heartbeat and tick["type"]=="HEARTBEAT"):
                    print(tick)
                    self.on_success(tick)


In [57]:
the_qvals[0][(1.16113, 99001), 'yes']
#max(the_qvals[0])

-1242.6687180930076

In [58]:
at = autoTrader(accountID=account_id, params={"instruments": "EUR_USD,"})

In [ ]:
print(config['oanda']['account_id'])
at.rates(account_id=config['oanda']['account_id'], instruments="EUR_USD", ignore_heartbeat=True)

101-001-1715738-001
{'type': 'PRICE', 'time': '2019-04-02T12:07:40.715004761Z', 'bids': [{'price': '1.12018', 'liquidity': 10000000}], 'asks': [{'price': '1.12030', 'liquidity': 10000000}], 'closeoutBid': '1.12003', 'closeoutAsk': '1.12045', 'status': 'tradeable', 'tradeable': True, 'instrument': 'EUR_USD'}
ticks =  1
closeout 1.12045 w
closeask 1.12113
                     closeoutAsk                            time
time                                                            
2019-04-02 12:07:40      1.12045  2019-04-02T12:07:40.715004761Z  dfrdfr
y:  -147.40875398667123 , n:  -228.10934963744054 , amount:  1001 , pos: 1
go long
	 {'orderCreateTransaction': {'type': 'MARKET_ORDER', 'instrument': 'EUR_USD', 'units': '1001', 'timeInForce': 'FOK', 'positionFill': 'DEFAULT', 'reason': 'CLIENT_ORDER', 'id': '862', 'accountID': '101-001-1715738-001', 'userID': 1715738, 'batchID': '862', 'requestID': '78576410132982904', 'time': '2019-04-02T12:07:50.018776018Z'}, 'orderFillTransaction': 

{'type': 'PRICE', 'time': '2019-04-02T12:08:25.893858323Z', 'bids': [{'price': '1.12025', 'liquidity': 10000000}], 'asks': [{'price': '1.12036', 'liquidity': 10000000}], 'closeoutBid': '1.12010', 'closeoutAsk': '1.12051', 'status': 'tradeable', 'tradeable': True, 'instrument': 'EUR_USD'}
ticks =  10
closeout 1.12045 w
closeask 1.12113
                     closeoutAsk                            time
time                                                            
2019-04-02 12:07:40      1.12045  2019-04-02T12:07:40.715004761Z
2019-04-02 12:07:45      1.12045  2019-04-02T12:07:51.226147307Z
2019-04-02 12:07:50      1.12045  2019-04-02T12:07:51.226147307Z
2019-04-02 12:07:55      1.12045  2019-04-02T12:07:57.591293461Z
2019-04-02 12:08:00      1.12047  2019-04-02T12:08:10.494452766Z
2019-04-02 12:08:05      1.12047  2019-04-02T12:08:10.494452766Z
2019-04-02 12:08:10      1.12047  2019-04-02T12:08:10.494452766Z
2019-04-02 12:08:15      1.12050  2019-04-02T12:08:21.066172024Z
2019-04-02 12

{'type': 'PRICE', 'time': '2019-04-02T12:09:08.069207436Z', 'bids': [{'price': '1.12014', 'liquidity': 10000000}], 'asks': [{'price': '1.12027', 'liquidity': 10000000}], 'closeoutBid': '1.11999', 'closeoutAsk': '1.12042', 'status': 'tradeable', 'tradeable': True, 'instrument': 'EUR_USD'}
ticks =  16
closeout 1.12045 w
closeask 1.12113
                     closeoutAsk                            time
time                                                            
2019-04-02 12:07:40      1.12045  2019-04-02T12:07:40.715004761Z
2019-04-02 12:07:45      1.12045  2019-04-02T12:07:51.226147307Z
2019-04-02 12:07:50      1.12045  2019-04-02T12:07:51.226147307Z
2019-04-02 12:07:55      1.12045  2019-04-02T12:07:57.591293461Z
2019-04-02 12:08:00      1.12047  2019-04-02T12:08:10.494452766Z
2019-04-02 12:08:05      1.12047  2019-04-02T12:08:10.494452766Z
2019-04-02 12:08:10      1.12047  2019-04-02T12:08:10.494452766Z
2019-04-02 12:08:15      1.12050  2019-04-02T12:08:21.066172024Z
2019-04-02 12

{'type': 'PRICE', 'time': '2019-04-02T12:09:10.632474419Z', 'bids': [{'price': '1.12013', 'liquidity': 10000000}], 'asks': [{'price': '1.12025', 'liquidity': 10000000}], 'closeoutBid': '1.11998', 'closeoutAsk': '1.12040', 'status': 'tradeable', 'tradeable': True, 'instrument': 'EUR_USD'}
ticks =  21
closeout 1.12045 w
closeask 1.12113
                     closeoutAsk                            time
time                                                            
2019-04-02 12:07:40      1.12045  2019-04-02T12:07:40.715004761Z
2019-04-02 12:07:45      1.12045  2019-04-02T12:07:51.226147307Z
2019-04-02 12:07:50      1.12045  2019-04-02T12:07:51.226147307Z
2019-04-02 12:07:55      1.12045  2019-04-02T12:07:57.591293461Z
2019-04-02 12:08:00      1.12047  2019-04-02T12:08:10.494452766Z
2019-04-02 12:08:05      1.12047  2019-04-02T12:08:10.494452766Z
2019-04-02 12:08:10      1.12047  2019-04-02T12:08:10.494452766Z
2019-04-02 12:08:15      1.12050  2019-04-02T12:08:21.066172024Z
2019-04-02 12

{'type': 'PRICE', 'time': '2019-04-02T12:09:22.656347451Z', 'bids': [{'price': '1.12000', 'liquidity': 10000000}], 'asks': [{'price': '1.12012', 'liquidity': 10000000}], 'closeoutBid': '1.11985', 'closeoutAsk': '1.12027', 'status': 'tradeable', 'tradeable': True, 'instrument': 'EUR_USD'}
ticks =  26
closeout 1.12045 w
closeask 1.12113
                     closeoutAsk                            time
time                                                            
2019-04-02 12:07:40      1.12045  2019-04-02T12:07:40.715004761Z
2019-04-02 12:07:45      1.12045  2019-04-02T12:07:51.226147307Z
2019-04-02 12:07:50      1.12045  2019-04-02T12:07:51.226147307Z
2019-04-02 12:07:55      1.12045  2019-04-02T12:07:57.591293461Z
2019-04-02 12:08:00      1.12047  2019-04-02T12:08:10.494452766Z
2019-04-02 12:08:05      1.12047  2019-04-02T12:08:10.494452766Z
2019-04-02 12:08:10      1.12047  2019-04-02T12:08:10.494452766Z
2019-04-02 12:08:15      1.12050  2019-04-02T12:08:21.066172024Z
2019-04-02 12

...

{'type': 'PRICE', 'time': '2019-04-02T12:18:30.489752354Z', 'bids': [{'price': '1.12033', 'liquidity': 10000000}], 'asks': [{'price': '1.12045', 'liquidity': 10000000}], 'closeoutBid': '1.12018', 'closeoutAsk': '1.12060', 'status': 'tradeable', 'tradeable': True, 'instrument': 'EUR_USD'}
ticks =  114
closeout 1.12045 w
closeask 1.12113
                     closeoutAsk                            time
time                                                            
2019-04-02 12:07:40      1.12045  2019-04-02T12:07:40.715004761Z
2019-04-02 12:07:45      1.12045  2019-04-02T12:07:51.226147307Z
2019-04-02 12:07:50      1.12045  2019-04-02T12:07:51.226147307Z
2019-04-02 12:07:55      1.12045  2019-04-02T12:07:57.591293461Z
2019-04-02 12:08:00      1.12047  2019-04-02T12:08:10.494452766Z
2019-04-02 12:08:05      1.12047  2019-04-02T12:08:10.494452766Z
2019-04-02 12:08:10      1.12047  2019-04-02T12:08:10.494452766Z
2019-04-02 12:08:15      1.12050  2019-04-02T12:08:21.066172024Z
2019-04-02 1

{'type': 'PRICE', 'time': '2019-04-02T12:18:36.489383912Z', 'bids': [{'price': '1.12035', 'liquidity': 10000000}], 'asks': [{'price': '1.12048', 'liquidity': 10000000}], 'closeoutBid': '1.12020', 'closeoutAsk': '1.12063', 'status': 'tradeable', 'tradeable': True, 'instrument': 'EUR_USD'}
ticks =  116
closeout 1.12045 w
closeask 1.12113
                     closeoutAsk                            time
time                                                            
2019-04-02 12:07:40      1.12045  2019-04-02T12:07:40.715004761Z
2019-04-02 12:07:45      1.12045  2019-04-02T12:07:51.226147307Z
2019-04-02 12:07:50      1.12045  2019-04-02T12:07:51.226147307Z
2019-04-02 12:07:55      1.12045  2019-04-02T12:07:57.591293461Z
2019-04-02 12:08:00      1.12047  2019-04-02T12:08:10.494452766Z
2019-04-02 12:08:05      1.12047  2019-04-02T12:08:10.494452766Z
2019-04-02 12:08:10      1.12047  2019-04-02T12:08:10.494452766Z
2019-04-02 12:08:15      1.12050  2019-04-02T12:08:21.066172024Z
2019-04-02 1

{'type': 'PRICE', 'time': '2019-04-02T12:18:43.555273466Z', 'bids': [{'price': '1.12035', 'liquidity': 10000000}], 'asks': [{'price': '1.12047', 'liquidity': 10000000}], 'closeoutBid': '1.12020', 'closeoutAsk': '1.12062', 'status': 'tradeable', 'tradeable': True, 'instrument': 'EUR_USD'}
ticks =  118
closeout 1.12045 w
closeask 1.12113
                     closeoutAsk                            time
time                                                            
2019-04-02 12:07:40      1.12045  2019-04-02T12:07:40.715004761Z
2019-04-02 12:07:45      1.12045  2019-04-02T12:07:51.226147307Z
2019-04-02 12:07:50      1.12045  2019-04-02T12:07:51.226147307Z
2019-04-02 12:07:55      1.12045  2019-04-02T12:07:57.591293461Z
2019-04-02 12:08:00      1.12047  2019-04-02T12:08:10.494452766Z
2019-04-02 12:08:05      1.12047  2019-04-02T12:08:10.494452766Z
2019-04-02 12:08:10      1.12047  2019-04-02T12:08:10.494452766Z
2019-04-02 12:08:15      1.12050  2019-04-02T12:08:21.066172024Z
2019-04-02 1

{'type': 'PRICE', 'time': '2019-04-02T12:18:55.610087440Z', 'bids': [{'price': '1.12040', 'liquidity': 10000000}], 'asks': [{'price': '1.12053', 'liquidity': 10000000}], 'closeoutBid': '1.12025', 'closeoutAsk': '1.12068', 'status': 'tradeable', 'tradeable': True, 'instrument': 'EUR_USD'}
ticks =  120
closeout 1.12045 w
closeask 1.12113
                     closeoutAsk                            time
time                                                            
2019-04-02 12:07:40      1.12045  2019-04-02T12:07:40.715004761Z
2019-04-02 12:07:45      1.12045  2019-04-02T12:07:51.226147307Z
2019-04-02 12:07:50      1.12045  2019-04-02T12:07:51.226147307Z
2019-04-02 12:07:55      1.12045  2019-04-02T12:07:57.591293461Z
2019-04-02 12:08:00      1.12047  2019-04-02T12:08:10.494452766Z
2019-04-02 12:08:05      1.12047  2019-04-02T12:08:10.494452766Z
2019-04-02 12:08:10      1.12047  2019-04-02T12:08:10.494452766Z
2019-04-02 12:08:15      1.12050  2019-04-02T12:08:21.066172024Z
2019-04-02 1

{'type': 'PRICE', 'time': '2019-04-02T12:19:00.636695702Z', 'bids': [{'price': '1.12036', 'liquidity': 10000000}], 'asks': [{'price': '1.12048', 'liquidity': 10000000}], 'closeoutBid': '1.12021', 'closeoutAsk': '1.12063', 'status': 'tradeable', 'tradeable': True, 'instrument': 'EUR_USD'}
ticks =  122
closeout 1.12045 w
closeask 1.12113
                     closeoutAsk                            time
time                                                            
2019-04-02 12:07:40      1.12045  2019-04-02T12:07:40.715004761Z
2019-04-02 12:07:45      1.12045  2019-04-02T12:07:51.226147307Z
2019-04-02 12:07:50      1.12045  2019-04-02T12:07:51.226147307Z
2019-04-02 12:07:55      1.12045  2019-04-02T12:07:57.591293461Z
2019-04-02 12:08:00      1.12047  2019-04-02T12:08:10.494452766Z
2019-04-02 12:08:05      1.12047  2019-04-02T12:08:10.494452766Z
2019-04-02 12:08:10      1.12047  2019-04-02T12:08:10.494452766Z
2019-04-02 12:08:15      1.12050  2019-04-02T12:08:21.066172024Z
2019-04-02 1

In [34]:
type(random.choice([1,2]))

int